In [9]:
import pandas as pd
from matplotlib import pyplot as plt
import numpy as np
import pickle
import plotly.express as px
import plotly.graph_objects as go

import dash
from dash import html,Input,Output,dcc
from dash.dependencies import Input, Output, State
import geopandas as gpd
from datetime import date


path = '../'

def load_augumented(code):
    file = path + 'data/augumented/' + code + '.pkl'
    with open(file, 'rb') as f:
        df = pickle.load(f)
    return df
countries = ["BG", "GR", "HR", "RO", "RS", "SI"]
country_dict = {
"BG":"Bulgaria",
"GR":"Greece",
"HR":"Croatia",
"RO":"Romania",
"RS":"Republic of Serbia",
"SI":"Slovenia",
}

In [33]:
code = 'BG'
df = load_augumented(code)
df.drop(columns=["Price-1","Price-2","Price-24","Load-1","Load-24"])

DayAheadPrice  GenBiomass  GenFossilBrownCoal  \
2022-01-02 00:00:00+00:00         102.85        33.0              2181.0   
2022-01-02 01:00:00+00:00          84.27        34.0              2121.0   
2022-01-02 02:00:00+00:00          39.53        33.0              2116.0   
2022-01-02 03:00:00+00:00          18.97        32.0              2119.0   
2022-01-02 04:00:00+00:00          18.97        32.0              2120.0   
...                                  ...         ...                 ...   
2022-11-26 03:00:00+00:00         197.99        32.0              2893.0   
2022-11-26 04:00:00+00:00         211.94        31.0              2814.0   
2022-11-26 05:00:00+00:00         214.94        31.0              2806.0   
2022-11-26 06:00:00+00:00         228.07        32.0              2935.0   
2022-11-26 07:00:00+00:00         264.96        32.0              2951.0   

                           GenFossilGas  GenFossilHardCoal  GenHydroPumped  \
2022-01-02 00:00:00+00:00         486.0               61.0             0.0   
2022-01-02 01:00:00+00:00         485.0               62.0             0.0   
2022-01-02 02:00:00+00:00         484.0               62.0             0.0   
2022-01-02 03:00:00+00:00         489.0               34.0             0.0   
2022-01-02 04:00:00+00:00         489.0               37.0             0.0   
...                                 ...                ...             ...   
2022-11-26 03:00:00+00:00         427.0               66.0             0.0   
2022-11-26 04:00:00+00:00         427.0               67.0             0.0   
2022-11-26 05:00:00+00:00         428.0               67.0             0.0   
2022-11-26 06:00:00+00:00         428.0               68.0             0.0   
2022-11-26 07:00:00+00:00         426.0               68.0             0.0   

                           GenHydroRiver  GenHydroReservoir  GenNuclear  \
2022-01-02 00:00:00+00:00          128.0               90.0      2168.0   
2022-01-02 01:00:00+00:00          128.0                8.0      2168.0   
2022-01-02 02:00:00+00:00          129.0                8.0      2170.0   
2022-01-02 03:00:00+00:00          132.0                7.0      2169.0   
2022-01-02 04:00:00+00:00          135.0                8.0      2167.0   
...                                  ...                ...         ...   
2022-11-26 03:00:00+00:00           90.0              125.0      2165.0   
2022-11-26 04:00:00+00:00          109.0               72.0      2164.0   
2022-11-26 05:00:00+00:00          147.0               90.0      2165.0   
2022-11-26 06:00:00+00:00          157.0              272.0      2165.0   
2022-11-26 07:00:00+00:00          156.0              382.0      2165.0   

                           GenSolar  ...  LoadActual  Temperature  \
2022-01-02 00:00:00+00:00       0.0  ...      3499.0          3.9   
2022-01-02 01:00:00+00:00       0.0  ...      3439.0          4.3   
2022-01-02 02:00:00+00:00       0.0  ...      3426.0          4.5   
2022-01-02 03:00:00+00:00       0.0  ...      3438.0          4.3   
2022-01-02 04:00:00+00:00       0.0  ...      3543.0          4.4   
...                             ...  ...         ...          ...   
2022-11-26 03:00:00+00:00       0.0  ...      3857.0         -0.4   
2022-11-26 04:00:00+00:00       0.0  ...      4027.0         -0.4   
2022-11-26 05:00:00+00:00      18.0  ...      4320.0         -0.1   
2022-11-26 06:00:00+00:00     221.0  ...      4674.0         -0.2   
2022-11-26 07:00:00+00:00     537.0  ...      4666.0          0.5   

                           Precipitation  SolarRad  PowerUnavailable  \
2022-01-02 00:00:00+00:00            0.0         0             874.0   
2022-01-02 01:00:00+00:00            0.0         0             874.0   
2022-01-02 02:00:00+00:00            0.0         0             874.0   
2022-01-02 03:00:00+00:00            0.0         0             874.0   
2022-01-02 04:00:00+00:00            0.0         0             874.0   
...            

In [34]:
gen_cols = []
imp_cols = []
fossil_cols = []
for col in df.columns:
    if col[:3] == 'Gen' and col[-5:] != "Total":
        gen_cols.append(col)
    if col[:6] == 'Import':
        imp_cols.append(col)
    if col[:9] == 'GenFossil':
        fossil_cols.append(col)
#display(gen_cols)
#for i, y in enumerate(gen_cols):
#    print(i,y)

In [43]:
colors = ['#e6194B', '#3cb44b', '#ffe119', '#4363d8', '#f58231', '#911eb4', '#42d4f4', '#f032e6', '#bfef45', '#fabed4', '#469990', '#dcbeff', '#9A6324', '#fffac8', '#800000', '#aaffc3', '#808000', '#ffd8b1', '#000075', '#a9a9a9', '#000000']
display(df.loc["2022-11"])

DayAheadPrice  GenBiomass  GenFossilBrownCoal  \
2022-11-25 12:00:00+00:00         245.03        33.0              2604.0   
2022-11-25 13:00:00+00:00         276.90        33.0              2651.0   
2022-11-25 14:00:00+00:00         317.23        33.0              2704.0   
2022-11-25 15:00:00+00:00         327.36        34.0              2740.0   
2022-11-25 16:00:00+00:00         349.90        33.0              2747.0   
2022-11-25 17:00:00+00:00         337.95        33.0              2743.0   
2022-11-25 18:00:00+00:00         324.42        34.0              2746.0   
2022-11-25 19:00:00+00:00         288.50        33.0              2742.0   
2022-11-25 20:00:00+00:00         266.32        31.0              2679.0   
2022-11-25 21:00:00+00:00         269.92        31.0              2727.0   
2022-11-25 22:00:00+00:00         226.03        31.0              2746.0   
2022-11-25 23:00:00+00:00         212.77        31.0              2821.0   
2022-11-26 00:00:00+00:00         210.70        33.0              2901.0   
2022-11-26 01:00:00+00:00         201.70        32.0              2931.0   
2022-11-26 02:00:00+00:00         200.00        32.0              2933.0   
2022-11-26 03:00:00+00:00         197.99        32.0              2893.0   
2022-11-26 04:00:00+00:00         211.94        31.0              2814.0   
2022-11-26 05:00:00+00:00         214.94        31.0              2806.0   
2022-11-26 06:00:00+00:00         228.07        32.0              2935.0   
2022-11-26 07:00:00+00:00         264.96        32.0              2951.0   

                           GenFossilGas  GenFossilHardCoal  GenHydroPumped  \
2022-11-25 12:00:00+00:00         424.0               61.0             0.0   
2022-11-25 13:00:00+00:00         422.0               62.0             0.0   
2022-11-25 14:00:00+00:00         424.0               62.0             0.0   
2022-11-25 15:00:00+00:00         425.0               63.0             0.0   
2022-11-25 16:00:00+00:00         423.0               63.0             0.0   
2022-11-25 17:00:00+00:00         422.0               62.0             0.0   
2022-11-25 18:00:00+00:00         427.0               62.0             0.0   
2022-11-25 19:00:00+00:00         425.0               62.0             0.0   
2022-11-25 20:00:00+00:00         423.0               62.0             0.0   
2022-11-25 21:00:00+00:00         424.0               66.0             0.0   
2022-11-25 22:00:00+00:00         420.0               66.0             0.0   
2022-11-25 23:00:00+00:00         423.0               66.0             0.0   
2022-11-26 00:00:00+00:00         423.0               67.0             0.0   
2022-11-26 01:00:00+00:00         424.0               67.0             0.0   
2022-11-26 02:00:00+00:00         425.0               67.0             0.0   
2022-11-26 03:00:00+00:00         427.0               66.0             0.0   
2022-11-26 04:00:00+00:00         427.0               67.0             0.0   
2022-11-26 05:00:00+00:00         428.0               67.0             0.0   
2022-11-26 06:00:00+00:00         428.0               68.0             0.0   
2022-11-26 07:00:00+00:00         426.0               68.0             0.0   

                           GenHydroRiver  GenHydroReservoir  GenNuclear  \
2022-11-25 12:00:00+00:00          100.0               42.0      2164.0   
2022-11-25 13:00:00+00:00          135.0              107.0      2163.0   
2022-11-25 14:00:00+00:00          206.0              287.0      2165.0   
2022-11-25 15:00:00+00:00          215.0              826.0      2164.0   
2022-11-25 16:00:00+00:00          218.0              989.0      2164.0   
2022-11-25 17:00:00+00:00          216.0              988.0      2165.0   
2022-11-25 18:00:00+00:00          215.0              740.0      2164.0   
2022-11-25 19:00:00+00:00          164.0              516.0      2165.0   
2022-11-25 20:00:00+00:00          144.0              426.0      2163.0   
2022-11-25 21:00:00+00:00          123.0 

In [36]:
def plotGeneration(roll_window=24):
        if roll_window!=0: copy = df.copy().rolling(window=roll_window).mean()
        else: copy = df.copy()

        fig = go.Figure()
        for i,col in enumerate(gen_cols):
                color = colors[i]
                visibility='legendonly'
                visibility=True
                fig.add_trace(go.Scatter(x=copy.index, 
                                        y=copy[col], 
                                        name=col,
                                        mode='lines',
                                        line_width=0,
                                        fillcolor=colors[i],
                                        stackgroup='one',
                                        visible=visibility))
                                        #groupnorm='percent'))
        fig.add_trace(go.Scatter(x=copy.index, 
                                y=copy["GenTotal"], 
                                name="GenTotal",
                                mode="lines",
                                line_color="black"))  
        #fig.add_trace(go.Scatter(x=df.index, y=df["DayAheadPrice"], name='High 2014'))
        #fig.add_trace(go.Scatter(x=df.index, y=df["DayAheadPrice"], name='High 2014'))
        fig.update_layout(
                title={'text':'Rolling Average of Power Generation in %s with window of %.i hours' % (country_dict[code], roll_window),
                       'x':0.5, 
                       'xanchor':'center'},
                yaxis_title='Power Generation (MW)',
                xaxis_title='Date',
                showlegend=True)
        fig.show()
plotGeneration(24)

In [37]:
def plotPrice(roll_window=24):
        roll_copy = df.copy().rolling(window=roll_window).mean()
        copy = df.copy()
        #if roll_window!=0: copy = df.copy().rolling(window=roll_window).mean()
        #else: copy = df.copy()

        fig = go.Figure()
        fig.add_trace(go.Scatter(x=copy.index, 
                                y=copy["DayAheadPrice"], 
                                name="GenTotal",
                                mode="lines",
                                line_color="black"))  
        fig.add_trace(go.Scatter(x=roll_copy.index, 
                                y=roll_copy["DayAheadPrice"], 
                                name="Rolling average %.i h" % (roll_window),
                                mode="lines",
                                line_color="red")) 
        fig.update_layout(
                title={'text':'Raw Data of Energy Prices in %s' % (country_dict[code]),
                       'x':0.5, 'xanchor':'center'},
                yaxis_title='Price (EUR/MWh)',
                xaxis_title='Date',
                showlegend=True)
        fig.show()
plotPrice(24)

In [38]:
from functions import *

In [39]:
def plotPricePrediction(roll_window=24):
        test_size=0.5
        model, params, selected_features, err, predictions = train_model_country('rf', df, 20, test_size=test_size)
        def train(dataframe):
                return dataframe[:int((1-test_size)*dataframe.shape[0])]
        def test(dataframe):
                return dataframe[int((1-test_size)*dataframe.shape[0]):]
        def rolling(dataframe):
                return dataframe.rolling(window=roll_window).mean()
        
        copy = df.copy()
        
        fig = go.Figure()
        fig.add_trace(go.Scatter(x=copy.index, 
                                y=copy["DayAheadPrice"], 
                                name="Train price",
                                mode="lines",
                                line_color="blue"))  
        fig.add_trace(go.Scatter(x=copy.index, 
                                y=rolling(copy)["DayAheadPrice"], 
                                name="Rolling average of train prive",
                                mode="lines",
                                line_color="midnightblue"))
        display(predictions)
        fig.add_trace(go.Scatter(x=predictions.index, 
                                y=predictions,
                                name="Prediction",
                                mode="lines",
                                line_color="orange"))  #
        fig.add_trace(go.Scatter(x=predictions.index, 
                                y=rolling(predictions), 
                                name="Rolling average of prediction",
                                mode="lines",
                                line_color="red"))  
        #fig.add_trace(go.Scatter(x=roll_copy.index, 
        #                        y=roll_copy["DayAheadPrice"], 
        #                        name="Rolling average %.i h" % (roll_window),
        #                        mode="lines",
        #                        line_color="red")) 
        fig.update_layout(
                title={'text':'Prediction of Energy Price in %s' % (country_dict[code]),'x':0.5, 'xanchor':'center'},
                yaxis_title='Price (EUR/MWh)',
                xaxis_title='Date',
                showlegend=True)
        return fig, selected_features, err, params
fig, selected_features, err, params = plotPricePrediction(24)

AttributeError: 'str' object has no attribute 'copy'

In [ ]:
fig.show()

In [ ]:
from dash import Dash, dash_table
import pandas as pd
def generate_table(series):
    frame = pd.DataFrame({'Metric':series.index, 'Value':series.values})
    return frame.to_html()
new = generate_table(err)

<table border="1" class="dataframe">
  <thead>
    <tr style="text-align: right;">
      <th></th>
      <th>Metric</th>
      <th>Value</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <th>0</th>
      <td>Root mean squared error</td>
      <td>58.682354</td>
    </tr>
    <tr>
      <th>1</th>
      <td>Coefficient of variation RMSE</td>
      <td>0.224217</td>
    </tr>
    <tr>
      <th>2</th>
      <td>Normalized mean bias error</td>
      <td>0.027412</td>
    </tr>
    <tr>
      <th>3</th>
      <td>R2 score</td>
      <td>0.873968</td>
    </tr>
  </tbody>
</table>


In [ ]:
def generate_table(dataframe, max_rows=10):
    return html.Table([
        #html.Thead(
        #    html.Tr([html.Th(col) for col in dataframe.columns])
        #),
        html.Tbody([
            html.Tr([
                html.Td(dataframe.iloc[i][col]) for col in dataframe.columns
            ]) for i in range(min(len(dataframe), max_rows))
        ])
    ])
frame = pd.DataFrame({'Metric':err.index, 'Value':err.values})
generate_table(frame)

Table([Tbody([Tr([Td('Root mean squared error'), Td(58.682354486395305)]), Tr([Td('Coefficient of variation RMSE'), Td(0.2242171307791625)]), Tr([Td('Normalized mean bias error'), Td(0.02741183078614439)]), Tr([Td('R2 score'), Td(0.8739677858843424)])])])

In [ ]:


dff = pd.read_csv('https://raw.githubusercontent.com/plotly/datasets/master/solar.csv')
display(dff)
dash_table.DataTable(dff.to_dict('records'), [{"name": i, "id": i} for i in dff.columns])

State  Number of Solar Plants  Installed Capacity (MW)  \
0      California                     289                     4395   
1         Arizona                      48                     1078   
2          Nevada                      11                      238   
3      New Mexico                      33                      261   
4        Colorado                      20                      118   
5           Texas                      12                      187   
6  North Carolina                     148                      669   
7        New York                      13                       53   

   Average MW Per Plant  Generation (GWh)  
0                  15.3             10826  
1                  22.5              2550  
2                  21.6               557  
3                   7.9               590  
4                   5.9               235  
5                  15.6               354  
6                   4.5              1162  
7                   4.1                84

DataTable(data=[{'State': 'California', 'Number of Solar Plants': 289, 'Installed Capacity (MW)': 4395, 'Average MW Per Plant': 15.3, 'Generation (GWh)': 10826}, {'State': 'Arizona', 'Number of Solar Plants': 48, 'Installed Capacity (MW)': 1078, 'Average MW Per Plant': 22.5, 'Generation (GWh)': 2550}, {'State': 'Nevada', 'Number of Solar Plants': 11, 'Installed Capacity (MW)': 238, 'Average MW Per Plant': 21.6, 'Generation (GWh)': 557}, {'State': 'New Mexico', 'Number of Solar Plants': 33, 'Installed Capacity (MW)': 261, 'Average MW Per Plant': 7.9, 'Generation (GWh)': 590}, {'State': 'Colorado', 'Number of Solar Plants': 20, 'Installed Capacity (MW)': 118, 'Average MW Per Plant': 5.9, 'Generation (GWh)': 235}, {'State': 'Texas', 'Number of Solar Plants': 12, 'Installed Capacity (MW)': 187, 'Average MW Per Plant': 15.6, 'Generation (GWh)': 354}, {'State': 'North Carolina', 'Number of Solar Plants': 148, 'Installed Capacity (MW)': 669, 'Average MW Per Plant': 4.5, 'Generation (GWh)': 11

In [66]:
df.tail()

DayAheadPrice  GenBiomass  GenFossilBrownCoal  \
2022-11-26 03:00:00+00:00         197.99        32.0              2893.0   
2022-11-26 04:00:00+00:00         211.94        31.0              2814.0   
2022-11-26 05:00:00+00:00         214.94        31.0              2806.0   
2022-11-26 06:00:00+00:00         228.07        32.0              2935.0   
2022-11-26 07:00:00+00:00         264.96        32.0              2951.0   

                           GenFossilGas  GenFossilHardCoal  GenHydroPumped  \
2022-11-26 03:00:00+00:00         427.0               66.0             0.0   
2022-11-26 04:00:00+00:00         427.0               67.0             0.0   
2022-11-26 05:00:00+00:00         428.0               67.0             0.0   
2022-11-26 06:00:00+00:00         428.0               68.0             0.0   
2022-11-26 07:00:00+00:00         426.0               68.0             0.0   

                           GenHydroRiver  GenHydroReservoir  GenNuclear  \
2022-11-26 03:00:00+00:00           90.0              125.0      2165.0   
2022-11-26 04:00:00+00:00          109.0               72.0      2164.0   
2022-11-26 05:00:00+00:00          147.0               90.0      2165.0   
2022-11-26 06:00:00+00:00          157.0              272.0      2165.0   
2022-11-26 07:00:00+00:00          156.0              382.0      2165.0   

                           GenSolar  ...  Price-1  Price-2  Price-24  Load-1  \
2022-11-26 03:00:00+00:00       0.0  ...   200.00   201.70    174.34  3789.0   
2022-11-26 04:00:00+00:00       0.0  ...   197.99   200.00    222.17  3857.0   
2022-11-26 05:00:00+00:00      18.0  ...   211.94   197.99    282.67  4027.0   
2022-11-26 06:00:00+00:00     221.0  ...   214.94   211.94    306.65  4320.0   
2022-11-26 07:00:00+00:00     537.0  ...   228.07   214.94    319.90  4674.0   

                           Load-24  GenTotal  ImportTotal  GenFossilTotal  \
2022-11-26 03:00:00+00:00   3738.0    6007.0        155.0          3386.0   
2022-11-26 04:00:00+00:00   4165.0    5894.0        127.0          3308.0   
2022-11-26 05:00:00+00:00   4626.0    5946.0        162.0          3301.0   
2022-11-26 06:00:00+00:00   4928.0    6443.0         48.0          3431.0   
2022-11-26 07:00:00+00:00   4955.0    6823.0          0.0          3445.0   

                           Hour  Month  
2022-11-26 03:00:00+00:00     3     11  
2022-11-26 04:00:00+00:00     4     11  
2022-11-26 05:00:00+00:00     5     11  
2022-11-26 06:00:00+00:00     6     11  
2022-11-26 07:00:00+00:00     7     11  

[5 rows x 32 columns]

In [ ]:
N = len(countries)
geoplot_columns = ["DayAheadPrice",'LoadActual']
n = len(geoplot_columns)
values = {"ISO":countries}
for i in range(n):
    values[geoplot_columns[i]]=np.zeros(N)
    
for i,code in enumerate(countries):
    df = load_augumented(code)
    copy = df.copy()
    for j,column in enumerate(geoplot_columns):
        values[column][i] = copy[column].mean()

indicators = pd.DataFrame.from_dict(values,orient='index').transpose()
indicators[geoplot_columns] = indicators[geoplot_columns].astype(float)
with open(path+'data/clean/balkan.pkl', 'rb') as f:
    geo = pickle.load(f)

merged = gpd.GeoDataFrame(geo.merge(indicators, on='ISO', how='left'))
display(merged)

ISO   COUNTRY                                           geometry  \
0  BG  Bulgaria  POLYGON ((22.93560 41.34213, 22.95590 41.35562...   
1  HR   Croatia  MULTIPOLYGON (((17.57853 42.94383, 17.51889 42...   
2  GR    Greece  MULTIPOLYGON (((21.08305 39.05666, 21.04527 39...   
3  RO   Romania  POLYGON ((24.31971 43.69664, 24.30778 43.69749...   
4  RS    Serbia  POLYGON ((20.07142 42.56091, 20.09993 42.65770...   
5  SI  Slovenia  POLYGON ((15.30709 45.62986, 15.29400 45.59454...   

   DayAheadPrice   LoadActual  
0     253.322808  4427.112414  
1     254.515821  2080.919228  
2     265.579306  5567.410229  
3     248.238944  6440.189218  
4     260.963912  3819.879559  
5     257.003230  1543.710161

In [65]:
value1 = 'LoadActual'
value2 = "DayAheadPrice"
def update_map(column):
    # Filter data by selection
    filtered_df = merged[[column, 'geometry', 'COUNTRY']]
    # Create the choropleth map
    fig = px.choropleth(
        filtered_df, 
        geojson=filtered_df.geometry, 
        locations=filtered_df.index, 
        scope="europe",
        color=column, 
        color_continuous_scale='reds', 
        #range_color=(240, 270), 
        projection='natural earth',
        #labels={'Energy Consumption':'Energy Consumption (kWh)'}
    )

    fig.update_geos(
        center=dict(lon=21, lat=43), 
        lataxis_range=[30, 45], 
        lonaxis_range=[9, 30]
    )    
    
    fig.update_layout(coloraxis_showscale=True,
                      margin={"r":0,"t":0,"l":0,"b":0})
    
    fig2 = px.bar(merged.sort_values(by=column), x='COUNTRY', y=column,
             color=column, color_continuous_scale='reds',
             labels={'pop':'population of Canada'}, height=400)
    
    mini =merged[column].min()
    maxi =merged[column].max()
    diff = mini*(maxi-mini)/maxi
    print(diff)
    fig2.update_yaxes(range=[mini-diff,maxi+diff])

    fig3 = go.Figure()
    x = merged["COUNTRY"]
    y1 = merged[value1]
    y2 = merged[value2]
    fig3.add_trace(go.Bar(
        x=x,
        y=y1,
        name=value1,
        marker_color='indianred'
    ))
    fig3.add_trace(go.Bar(
        x=x,
        y=y2,
        name=value2,
        marker_color='lightsalmon'
    ))
    return fig,fig2, fig3
fig1,fig2,fig3=update_map(value2)
fig1.show()
fig2.show()
fig3.show()

16.20816541317522


In [2]:
def day_split(data_country, features, day):
    y = data_country['DayAheadPrice']
    x = data_country[features]
    x_train, x_test, y_train, y_test = x[x.index<day], x[day], y[y.index<day], y[day]
    return x_train, x_test, y_train, y_test
df.columns
fl = ['GenBiomass', 'GenFossilBrownCoal', 'GenFossilGas',
       'GenFossilHardCoal', 'GenHydroPumped', 'GenHydroRiver',
       'GenHydroReservoir', 'GenNuclear', 'GenSolar', 'GenWaste', 'GenWind',
       'ImportGR', 'ImportMK', 'ImportRO', 'ImportRS', 'ImportTR',
       'LoadActual', 'Temperature']
x_train, x_test, y_train, y_test = day_split(df,fl,day)
display(x_train.tail())
display(x_test.head())

NameError: name 'df' is not defined

In [17]:
def day_split(data_country, features, day):
    data_country = data_country.dropna()
    y = data_country['DayAheadPrice']
    x = data_country[features]
    x_train, x_test, y_train, y_test = x[x.index<day], x[day], y[y.index<day], y[day]
    return x_train, x_test, y_train, y_test
def train_model_country_day(data_country_input, day, n_features,model_type="rf", model_parameters=None):
    """
    Train a ML model. This function does the following:
        1. rescales the input data
        2. train test split
        3. feature selection on the training data
        4. train the model: either NN or RF
    
    Parameters:
        model_type: 'rf' | 'nn' | 'lr', str
            type of the model to train, 'rf' for random forest, 'lr' for linear regression and 'nn' for neural network
        data_country: DataFrame
            cleaned data for a given country (no Nans etc)
        n_features: int
            number of best features to select
        model_parameters: dict
            dictionary with model parameters, which are parameters for either 
            MLPRegressor or RandomForestRegressor from sklearn
    
    
    Out:
        model: object
            sklearn model
        params: DataFrame
            parameters used for rescaling the data; predictions have to be scaled back 
            for error calculation and out-of-sample new data must be scaled using these params
        selected_features: list or Index, not sure
            features used in training this model
        err: Series
            errors for predictions
    """
    data_country = data_country_input.copy()
    data_country, params = rescale(data_country)

    x_train, x_test, y_train, y_test = day_split(data_country, data_country.columns[1:],day)
    selected_features = get_best_features(x_train, n_features)

    x_train = x_train[selected_features]
    x_test = x_test[selected_features]

    if model_type.lower() == 'nn':
        if model_parameters == None:
            # these parameters worked okay for project 1
            model_parameters = {
                'hidden_layer_sizes': (16,16,14)
            }
        model = MLPRegressor(**model_parameters)
    elif model_type.lower() == 'lr':
       model = linear_model.LinearRegression() 
    elif model_type.lower() == 'rf':
        if model_parameters == None:
            # these parameters worked okay for project 1
            model_parameters = {
                'bootstrap': True,
                'min_samples_leaf': 2,
                'n_estimators': 10, 
                'min_samples_split': 3,
                'max_features': 10,
                'max_depth': 10,
                'max_leaf_nodes': None}
            
        model = RandomForestRegressor(**model_parameters)

    model.fit(x_train, y_train)
    predictions = model.predict(x_test)

    predictions = pd.Series(predictions, index=y_test.index).sort_index()
    y_test = y_test.sort_index()


    # to calculate errors, we have to rescale the data back using original parameters
    predictions = predictions * params.loc['DayAheadPrice', 'Std'] + params.loc['DayAheadPrice', 'Mean']
    y_test = y_test * params.loc['DayAheadPrice', 'Std'] + params.loc['DayAheadPrice', 'Mean']
    err = get_errors(y_test, predictions)

    #display(err)
    #plot_predictions(y_test, predictions)
    
    return model, params, selected_features, err, predictions


In [20]:
#train_model_country_day(data_country_input, day, n_features, model_type="rf", model_parameters=None)
from plotly.subplots import make_subplots
def plotDayPrediction(day,n_features,model_type='rf',exclude_features=["Price-1","Price-2"]):
        countries = ["BG", "HR", "RO", "RS", "SI"]
        countries_clean=[]
        for i,code in enumerate(countries):
                print(i,code)
                try: 
                        load_augumented(code).loc[day]
                except: print("Date for this day does not exist") 
                else: countries_clean.append(code)
        print(countries_clean)
        n = len(countries_clean)
        fig = make_subplots(rows=n, cols=1)
        def predOneDayOneCode(code,row,col):
                df = load_augumented(code).drop(columns=exclude_features)
                model, params, selected_features, err, predictions = train_model_country_day(df, day, 12, model_type="rf")
                def rolling(dataframe):
                        return dataframe.rolling(window=roll_window).mean()
                
                
                
                df = df.loc[day]

                fig.add_trace(go.Scatter(x=df.index, 
                                        y=df["DayAheadPrice"], 
                                        name="Real price",
                                        mode="lines",
                                        line_color="blue",),
                                        row=row,col=col)  
                
                fig.add_trace(go.Scatter(x=predictions.index, 
                                        y=predictions, 
                                        name="Prediction",
                                        mode="lines",
                                        line_color="orange",),
                                        row=row,col=col)  #

                fig.update_layout(
                        #title={'text':'Prediction of Energy Price in %s' % (country_dict[code]),'x':0.5, 'xanchor':'center'},
                        yaxis_title='Price (EUR/MWh)',
                        xaxis_title='Date',
                        showlegend=True)
                
                #return fig, selected_features, err
                return 0
        #figa=[None]*n
        #sfa=[None]*n
        #erra=[None]*n
        for i,code in enumerate(countries_clean):
                print(code)
                predOneDayOneCode(code,i+1,1)
        #code = "SI"
        #figa, sfa, erra=predOneDayOneCode(code,1,1)
        #print("aaskdjflöaksjdlfkjaskldjfkajdfölaj")
        fig.update_layout(legend=dict(
                orientation="h",
                entrywidth=120,
                yanchor="bottom",
                y=1.02,
                xanchor="right",
                x=1
                ))
        return fig,sfa,erra
figa, sfa, erra = plotDayPrediction("2022-06-03",12)
figa.show()

0 BG
1 HR
2 RO
3 RS
4 SI
['BG', 'HR', 'RO', 'RS', 'SI']
BG


<ipython-input-17-e893e9d7c62c>:5: FutureWarning:

Indexing a DataFrame with a datetimelike index using a single string to slice the rows, like `frame[string]`, is deprecated and will be removed in a future version. Use `frame.loc[string]` instead.



HR


<ipython-input-17-e893e9d7c62c>:5: FutureWarning:

Indexing a DataFrame with a datetimelike index using a single string to slice the rows, like `frame[string]`, is deprecated and will be removed in a future version. Use `frame.loc[string]` instead.



RO


<ipython-input-17-e893e9d7c62c>:5: FutureWarning:

Indexing a DataFrame with a datetimelike index using a single string to slice the rows, like `frame[string]`, is deprecated and will be removed in a future version. Use `frame.loc[string]` instead.



RS


KeyError: '2022-06-03'